# CptS 481 - Python Software Construction

## Unit 13: Checking and Debugging

In [31]:
from IPython.display import HTML
HTML(open("../include/notes.css", "r").read())

### pylint

``pylint`` takes a "picky" approach to code analysis. The "``lint``" part of the name comes from an early C program checker.

We start with the same "``0_sloppy.py``" file:

In [1]:
%%file 0_sloppy.py
import time

class Aclass:

    def __init__(self):
        return None
    
    def aMethod(self, var1, var2):
        self.var3 = var1*var2

    def bMethod(self):
        '''
        A simple function
        '''
        pass
        
def main():
    int = 10
    time = 'today'
    aObj = Aclass()
    aObj.var3 = 0
    val1 = 13.0
    flag = 0    
    if (int == 10):
        flagg = 1

    if (flag):
        print('Flag has been set: ')

    aObj.afunc(int, val1)
    print(aObj.var3)
    
main()

Overwriting 0_sloppy.py


In [2]:
%%sh
python3 -m pylint demos/0_sloppy.py || exit 0 # make Notebook ignore error status

************* Module 0_sloppy
demos/0_sloppy.py:7:0: C0303: Trailing whitespace (trailing-whitespace)
demos/0_sloppy.py:17:12: C0303: Trailing whitespace (trailing-whitespace)
demos/0_sloppy.py:18:0: C0325: Unnecessary parens after 'if' keyword (superfluous-parens)
demos/0_sloppy.py:21:0: C0325: Unnecessary parens after 'if' keyword (superfluous-parens)
demos/0_sloppy.py:26:0: C0303: Trailing whitespace (trailing-whitespace)
demos/0_sloppy.py:1:0: C0103: Module name "0_sloppy" doesn't conform to snake_case naming style (invalid-name)
demos/0_sloppy.py:1:0: C0114: Missing module docstring (missing-module-docstring)
demos/0_sloppy.py:3:0: C0115: Missing class docstring (missing-class-docstring)
demos/0_sloppy.py:8:4: C0116: Missing function or method docstring (missing-function-docstring)
demos/0_sloppy.py:3:0: R0903: Too few public methods (1/2) (too-few-public-methods)
demos/0_sloppy.py:9:8: W0201: Attribute 'var3' defined outside __init__ (attribute-defined-outside-init)
demos/0_slopp

So if we clean this up a bit...

In [3]:
%%file demos/2_pylint_tidy.py
"""
small script containing some potential bugs
"""
#pylint: disable=C0103

__pychecker__ = 'initattr classdoc funcdoc'

class Aclass:
    """
    This is a class.
    """
    def __init__(self):
        self.var3 = None

    def afunc(self, var1, var2):
        '''
        A simple function
        '''
        self.var3 = var1*var2

    def bfunc(self):
        '''
        A simple function
        '''
        pass

def main():
    '''
    The main function
    '''
    _int = 10
    aObj = Aclass()
    aObj.var3 = 0
    val1 = 13.0
    flag = 0
    if int == 10:
        flag = 1

    if flag:
        print('Flag has been set: ')

    aObj.afunc(_int, val1)
    print(aObj.var3)

main()

Overwriting demos/2_pylint_tidy.py


In [4]:
%%sh
pylint demos/2_pylint_tidy.py || exit 0 # make Notebook ignore error status

************* Module 2_pylint_tidy
demos/2_pylint_tidy.py:25:8: W0107: Unnecessary pass statement (unnecessary-pass)

------------------------------------------------------------------
Your code has been rated at 9.52/10 (previous run: 9.52/10, +0.00)



Let's try a more useful program:  "``3_polar_for_sphinx.py``".

In [5]:
"""
The ``polar`` Module
"""
from math import sin, cos, atan2, pi

__version__ = "1.0"

class Polar:
    """
    specifies a 2D position or velocity in polar coordinatesThes

    This class represents a 2D position or velocity measured in polar
    coordinates and defined by its `distance` (or speed) and an angle
    (`bearing`) (in radians) from the positive y ('North') direction.

    We follow the conventions of navigation, not mathematics, so 0
    degrees is North and bearings increase in a clockwise fashion.
    """

    DEGREES_TO_RADIANS = pi / 180
    "multiplicative constant to convert degrees to radians"

    #: multiplicative constant to convert radians to degrees
    RADIANS_TO_DEGREES = 180 / pi

    def __init__(self, distance=0.0, bearing=0.0):
        """
        specifies a polar point by `distance` and `bearing`
        """
        self.distance = distance
        self.bearing = bearing

    def rect(self):
        """
        returns the rectangular (Cartesian) coords as an (x, y) tuple
        """
        return (self.distance*sin(self.bearing),
                self.distance*cos(self.bearing))

    def __add__(self, other):
        """
        returns the result of adding two `Polar`s
        """
        (x0, y0) = self.rect()
        (x1, y1) = other.rect()
        dx = x1 + x0
        dy = y1 + y0
        mag = (dx**2 + dy**2)**0.5
        return Polar(mag, atan2(dy, dx) if mag > 0 else 0)

    def __repr__(self):
        """
        returns a 'lossless' string representation of a PolarCoordinate
        """
        return "Polar({}, {})".format(self.distance, self.bearing)


if __name__ == '__main__':
    # test1: with a 3-4-5 right triangle
    a = Polar(3, 0)
    print('  a:', a)
    b = Polar(4, pi/2)
    print('  b:', b)
    print('a+b:', a+b)

    # test2: zero relative distance
    c = Polar(2, Polar.DEGREES_TO_RADIANS * 30)
    print('  c:', c)
    d = Polar(2, Polar.DEGREES_TO_RADIANS * 210)
    print('  d:', d)
    print('c+d:', c+d)

  a: Polar(3, 0)
  b: Polar(4, 1.5707963267948966)
a+b: Polar(5.0, 0.6435011087932845)
  c: Polar(2, 0.5235987755982988)
  d: Polar(2, 3.6651914291880923)
c+d: Polar(4.002966042486721e-16, 2.5535900500422257)


In [6]:
%%sh
pylint demos/3_polar_for_sphinx.py || exit 0 # make Notebook ignore error status

************* Module 3_polar_for_sphinx
demos/3_polar_for_sphinx.py:1:0: C0103: Module name "3_polar_for_sphinx" doesn't conform to snake_case naming style (invalid-name)
demos/3_polar_for_sphinx.py:44:9: C0103: Variable name "x0" doesn't conform to snake_case naming style (invalid-name)
demos/3_polar_for_sphinx.py:44:13: C0103: Variable name "y0" doesn't conform to snake_case naming style (invalid-name)
demos/3_polar_for_sphinx.py:45:9: C0103: Variable name "x1" doesn't conform to snake_case naming style (invalid-name)
demos/3_polar_for_sphinx.py:45:13: C0103: Variable name "y1" doesn't conform to snake_case naming style (invalid-name)
demos/3_polar_for_sphinx.py:46:8: C0103: Variable name "dx" doesn't conform to snake_case naming style (invalid-name)
demos/3_polar_for_sphinx.py:47:8: C0103: Variable name "dy" doesn't conform to snake_case naming style (invalid-name)

------------------------------------------------------------------
Your code has been rated at 7.74/10 (previous run: 

In [7]:
%%sh
pylint --generate-rcfile

[MASTER]

# A comma-separated list of package or module names from where C extensions may
# be loaded. Extensions are loading into the active Python interpreter and may
# run arbitrary code.
extension-pkg-whitelist=

# Specify a score threshold to be exceeded before program exits with error.
fail-under=10.0

# Add files or directories to the blacklist. They should be base names, not
# paths.
ignore=CVS

# Add files or directories matching the regex patterns to the blacklist. The
# regex matches against base names, not paths.
ignore-patterns=

# Python code to execute, usually for sys.path manipulation such as
# pygtk.require().
#init-hook=

# Use multiple processes to speed up Pylint. Specifying 0 will auto-detect the
# number of processors available to use.
jobs=1

# Control the amount of potential inferred values when inferring a single
# object. This can help the performance when dealing with large functions or
# complex, nested conditions.
limit-inference-results=100

# List of plu

In [10]:
%%sh
ls -ad ~/.*rc

/home/bobl/.asoundrc
/home/bobl/.bashrc
/home/bobl/.cvsrc
/home/bobl/.dmrc
/home/bobl/.fbrc
/home/bobl/.gqcamrc
/home/bobl/.hxplayerrc
/home/bobl/.idlerc
/home/bobl/.joverc
/home/bobl/.mcoprc
/home/bobl/.mtinkrc
/home/bobl/.mtoolsrc
/home/bobl/.muttrc
/home/bobl/.nvidia-settings-rc
/home/bobl/.realplayerrc
/home/bobl/.ripperXrc
/home/bobl/.sversionrc
/home/bobl/.xdvirc
/home/bobl/.xpdfrc


### pdb

Here's a little program, "``4_faro_py2k.py``" written in Python 2K.

In [12]:
%%file demos/4_faro_py2k.py
"""
This program explores the non-randomness of the traditional 'faro'
method of card shuffling.  No matter how many cards there are in a
deck, there is always a finite number of faro shuffles that will
restore their original order.  (Of course, a faro shuffle is very hard
to do in practice!)
"""


def faroShuffle(oldDeck):
    """
    performs a 'faro' or 'perfect' shuffle

    `oldDeck` (a sequence) is the original deck.  The shuffled deck is
    returned.  It does an 'out' shuffle (top and bottom cards
    preserved).
    """
    # Look how easy Python makes this!
    n = len(oldDeck)
    newDeck = n*[ 0 ] # initializes result
    newDeck[0:n-1:2] = oldDeck[:n/2] # insert left hand
    newDeck[1:n:2]   = oldDeck[n/2:] # insert right hand
    return newDeck

def countShuffles(nCards):
    """
    counts the number of faro shuffles required to restore a deck

    `nCards` is the number of cards in the deck.  It must be an even
    positive int.
    """
    originalDeck = range(nCards)
    currentDeck = originalDeck
    shuffleCount = 0
    while True:
        shuffledDeck = faroShuffle(currentDeck)
        shuffleCount += 1
        if shuffledDeck == originalDeck:
            return shuffleCount
        currentDeck = shuffledDeck


nCards = 52
print '''
The ordering of a deck of {0} cards is restored after {1} faro shuffles.
'''.format(nCards, countShuffles(nCards))

Overwriting demos/4_faro_py2k.py


Run with Python2K, it runs fine:

In [13]:
%%sh
python2 demos/4_faro_py2k.py


The ordering of a deck of 52 cards is restored after 8 faro shuffles.



But in Python3K, there are problems. (If you're running this in your own IPython Notebook, session, you may need to interrupt the kernel.)

In [14]:
%%sh
python3 demos/4_faro_py2k.py || exit 0 # make Notebook ignore error status

  File "demos/4_faro_py2k.py", line 46
    print '''
The ordering of a deck of {0} cards is restored after {1} faro shuffles.
'''.format(nCards, countShuffles(nCards))
          ^
SyntaxError: invalid syntax


So one thing we clearly have to do is change the ``print`` statement to a function call (in ``5_faro_new_print.py``):

In [17]:
%%file demos/5_faro_new_print.py
"""
This program explores the non-randomness of the traditional 'faro'
method of card shuffling.  No matter how many cards there are in a
deck, there is always a finite number of faro shuffles that will
restore their original order.  (Of course, a faro shuffle is very hard
to do in practice!)
"""

def faroShuffle(oldDeck):
    """
    performs a 'faro' or 'perfect' shuffle

    `oldDeck` (a sequence) is the original deck.  The shuffled deck is
    returned.  It does an 'out' shuffle (top and bottom cards
    preserved).
    """
    # Look how easy Python makes this!
    n = len(oldDeck)
    newDeck = n*[ 0 ] # initializes result
    newDeck[0:n-1:2] = oldDeck[:n/2] # insert left hand
    newDeck[1:n:2]   = oldDeck[n/2:] # insert right hand
    return newDeck


def countShuffles(nCards):
    """
    counts the number of faro shuffles required to restore a deck

    `nCards` is the number of cards in the deck.  It must be an even
    positive int.
    """
    originalDeck = range(nCards)
    currentDeck = originalDeck
    shuffleCount = 0
    while True:
        shuffledDeck = faroShuffle(currentDeck)
        shuffleCount += 1
        if shuffledDeck == originalDeck:
            return shuffleCount
        currentDeck = shuffledDeck


if __name__ == '__main__':
    nCards = 52
    print('''
The ordering of a deck of {0} cards is restored after {1} faro shuffles.
'''[1:-1].format(nCards, countShuffles(nCards)))


Overwriting demos/5_faro_new_print.py


And if we run this...

In [18]:
%%sh
python3 demos/5_faro_new_print.py || exit 0 # make Notebook ignore error status

Traceback (most recent call last):
  File "demos/5_faro_new_print.py", line 47, in <module>
    '''[1:-1].format(nCards, countShuffles(nCards)))
  File "demos/5_faro_new_print.py", line 36, in countShuffles
    shuffledDeck = faroShuffle(currentDeck)
  File "demos/5_faro_new_print.py", line 20, in faroShuffle
    newDeck[0:n-1:2] = oldDeck[:n/2] # insert left hand
TypeError: slice indices must be integers or None or have an __index__ method


So what's the error here? We fix that and the result (in ``6_faro_floor_div.py``) is:

In [19]:
%%file demos/6_faro_floordiv.py
"""
This program explores the non-randomness of the traditional 'faro'
method of card shuffling.  No matter how many cards there are in a
deck, there is always a finite number of faro shuffles that will
restore their original order.  (Of course, a faro shuffle is very hard
to do in practice!)
"""

def faroShuffle(oldDeck):
    """
    performs a 'faro' or 'perfect' shuffle

    `oldDeck` (a sequence) is the original deck.  The shuffled deck is
    returned.  It does an 'out' shuffle (top and bottom cards
    preserved).
    """
    # Look how easy Python makes this!
    n = len(oldDeck)
    newDeck = n*[ 0 ] # initializes result
    newDeck[0:n-1:2] = oldDeck[:n//2] # insert left hand
    newDeck[1:n:2]   = oldDeck[n//2:] # insert right hand
    return newDeck


def countShuffles(nCards):
    """
    counts the number of faro shuffles required to restore a deck

    `nCards` is the number of cards in the deck.  It must be an even
    positive int.
    """
    originalDeck = range(nCards)
    currentDeck = originalDeck
    shuffleCount = 0
    while True:
        shuffledDeck = faroShuffle(currentDeck)
        shuffleCount += 1
        if shuffledDeck == originalDeck:
            return shuffleCount
        currentDeck = shuffledDeck


if __name__ == '__main__':
    nCards = 52
    print('''
The ordering of a deck of {0} cards is restored after {1} faro shuffles.
'''[1:-1].format(nCards, countShuffles(nCards)))


Overwriting demos/6_faro_floordiv.py


But if we try to run this, the code starts running but seems to be looping indefinitely. (If you're running this in your own IPython Notebook, session, be prepared to interrupt the kernel.)

This is a job for ``pdb``. By importing that module, we can, for instance, start the debugger at any time during execution.

In [ ]:
%%file demos/7_faro_for_pdb.py
"""
This program explores the non-randomness of the traditional 'faro'
method of card shuffling.  No matter how many cards there are in a
deck, there is always a finite number of faro shuffles that will
restore their original order.  (Of course, a faro shuffle is very hard
to do in practice!)
"""
import pdb

def faroShuffle(oldDeck):
    """
    performs a 'faro' or 'perfect' shuffle

    `oldDeck` (a sequence) is the original deck.  The shuffled deck is
    returned.  It does an 'out' shuffle (top and bottom cards
    preserved).
    """
    # Look how easy Python makes this!
    n = len(oldDeck)
    newDeck = n*[ 0 ] # initializes result
    newDeck[0:n-1:2] = oldDeck[:n//2] # insert left hand
    newDeck[1:n:2]   = oldDeck[n//2:] # insert right hand
    return newDeck


def countShuffles(nCards):
    """
    counts the number of faro shuffles required to restore a deck

    `nCards` is the number of cards in the deck.  It must be an even
    positive int.
    """
    originalDeck = range(nCards)
    currentDeck = originalDeck
    shuffleCount = 0
    while True:
        shuffledDeck = faroShuffle(currentDeck)
        shuffleCount += 1
        if shuffleCount == 8:
            pdb.set_trace()
        if shuffledDeck == originalDeck:
            return shuffleCount
        currentDeck = shuffledDeck


if __name__ == '__main__':
    nCards = 52
    print('''
The ordering of a deck of {0} cards is restored after {1} faro shuffles.
'''[1:-1].format(nCards, countShuffles(nCards)))


And here's the final version:

In [20]:
%%file demos/8_faro_fixed.py
"""
This program explores the non-randomness of the traditional 'faro'
method of card shuffling.  No matter how many cards there are in a
deck, there is always a finite number of faro shuffles that will
restore their original order.  (Of course, a faro shuffle is very hard
to do in practice!)
"""

from print_whence import printWhence


def faroShuffle(oldDeck, outShuffle=True):
    """
    performs a 'faro' or 'perfect' shuffle

    `oldDeck` (a sequence) is the original deck.  The shuffled deck is
    returned.  Iff `outShuffle` is True, it does an 'out' shuffle (top
    and bottom cards preserved).  If it is False, it does an 'in'
    shuffle.
    """
    # Look how easy Python makes this!
    n = len(oldDeck)
    newDeck = n*[ 0 ] # initializes result
    if outShuffle:
        newDeck[0:n-1:2] = oldDeck[:n//2] # insert left hand
        newDeck[1:n:2]   = oldDeck[n//2:] # insert right hand
    else:
        newDeck[0:n-1:2] = oldDeck[n//2:] # insert left hand
        newDeck[1:n:2]   = oldDeck[:n//2] # insert right hand
    return newDeck


def countShuffles(nCards):
    """
    counts the number of faro shuffles required to restore a deck

    `nCards` is the number of cards in the deck.  It must be an even
    positive int.
    """
    originalDeck = list(range(nCards))
    currentDeck = originalDeck
    shuffleCount = 0
    while True:
        shuffledDeck = faroShuffle(currentDeck)
        shuffleCount += 1
        if shuffledDeck == originalDeck:
            return shuffleCount
        currentDeck = shuffledDeck


if __name__ == '__main__':
    nCards = 52
    print('The ordering of a deck of {} cards is'
           ' restored after {} faro shuffles.'.format(
               nCards, countShuffles(nCards)))


Overwriting demos/8_faro_fixed.py


In [21]:
%%sh
python3 demos/8_faro_fixed.py

The ordering of a deck of 52 cards is restored after 8 faro shuffles.


### Scaffolding

Interactive debugging with ``pdb`` or another IDE is all well and good, but these days I use an alternative: scaffolding. Let's start with the module ``print_whence.py``. (It's in the unit directory with the demos.) Here it is:

In [22]:
import os
import inspect


def printWhence(comment=""):
    """prints a tag identifying the caller's file and line number

    This is mainly for debugging.
    """
    currentFrame = inspect.currentframe()
    callerFrame = currentFrame.f_back
    traceback = inspect.getframeinfo(callerFrame)

    # We assume that all file names being debugged are unique, so we
    # strip off directory information (if any).
    (_, fname) = os.path.split(traceback.filename)

    print("==== at {}:{}".format(
            fname, traceback.lineno), end="")
    if comment:
        print(" ({}) ".format(comment), end="")
    print(" ====")

When called, it prints out the name and line number of the file it's called from. That's not very useful from Jupyter Notebook:

In [25]:
printWhence()

==== at <ipython-input-25-e4a2c44f6fde>:2 ====


But it is useful in demos (which we'll now illustrate).

I recommend its use in "scaffolding": Adding additional temporary code to a Python module to display its progress. I recommend the following pattern: 